In [1]:
sys.path.insert(1, '../FrenetSerretMeanShape')
from frenet_path import *
from trajectory import *
from model_curvatures import *
from estimation_algo_utils import *
from maths_utils import *
from simu_utils import *
from visu_utils import *
from pre_process_Mocaplab_data import take_numpy_subset, barycenter_from_3ptsHand
import numpy as np
from pickle import *
import dill as pickle
import sys
import os.path

INFO: Using numpy backend


In [2]:
path = r"/home/pchassat/Documents/frenet-serret-smoothing/data/Repetitions_LSF/SMI2_X0077_1.csv"
# path = r"/home/pchassat/Documents/frenet-serret-smoothing/data/LSFtraj/RO1_X0024.Titres2.csv"
hand_barycentre = barycenter_from_3ptsHand(path, plot=False)
segment = [0, 100000]
data_traj = take_numpy_subset(hand_barycentre, segment[0], segment[1])
t = np.linspace(0,1,len(data_traj))
print(data_traj.shape)

# T_max = len(data_traj)*0.01
# bornes = [[0.92,1.44], [1.84, 2.28], [3.04, 3.16], [3.48, 3.6], [3.92, 4.24], [4.44, 4.8], [5.2, 5.64], [6.28, 6.4], [6.8, 7.32], [7.68, 8.04], [8.36, 9.44]]
# bornes = np.array(bornes)/T_max
# print(bornes)
# bornes_ind = np.rint(bornes*len(data_traj))

features = [data_traj]
# for i in range(bornes.shape[0]):
#     features.append(data_traj[int(bornes_ind[i][0]):int(bornes_ind[i][1]),:])
plot_3D_means(features, [], " ", "")

(564, 3)


In [3]:
param_loc_poly_deriv = { "h_min" : 0.01, "h_max" : 0.01, "nb_h" : 20}
param_loc_poly_TNB = {"h" : 50, "p" : 3, "iflag": [1,1], "ibound" : 1}
X_new, X, Q_LP, Q_GS, theta_extrins, successLocPoly = pre_process_data(data_traj, t, 1000, param_loc_poly_deriv, param_loc_poly_TNB, scale_ind={"ind":True,"val":1}, locpolyTNB_local=True)

In [4]:
s = interp1d(t, X.S(t))

In [5]:
plot_2D(t, X.S(t))
plot_2D(t, s(t))
plot_2D(t, X.Sdot(t))
from scipy.misc import derivative
Sdotdot = derivative(X.Sdot, t, dx=1e-6)
plot_2D(t, Sdotdot)
Sdotdotdot = derivative(X.Sdot, t, dx=1e-6, n=2)
plot_2D(t, Sdotdotdot)
# [0.31375765 0.41639496 0.51751123 0.60061497 0.77798819]

In [6]:
from scipy.interpolate import interp1d
t_new = np.linspace(0,1,3000)
invS = interp1d(X.S(t_new), t_new)

In [29]:
bornes_s = s(np.concatenate(bornes)).reshape((bornes.shape))
print(bornes_s)

[[0.03504079 0.11221673]
 [0.15450745 0.20862865]
 [0.25727263 0.26309177]
 [0.27765657 0.29215766]
 [0.31637596 0.34295819]
 [0.35703776 0.38446695]
 [0.4137996  0.4592425 ]
 [0.50720196 0.52595002]
 [0.5668804  0.64558603]
 [0.66746242 0.72658252]
 [0.77149258 0.94727676]]


In [30]:
plot_3D([Q_GS.data[:,0,:].transpose()], "initial trajectory")

In [7]:
h = 0.002
Q_GS.compute_neighbors(h)
mKappa, mTau, mS, mOmega, gam, ind_conv = compute_raw_curvatures(Q_GS, h, Q_GS, False)

In [11]:
plot_2D(mS, mKappa)
plot_2D(mS, mTau)

bornes_s = [[0.1199, 0.3259, 0.437, 0.662, 0.948]]
bornes = invS(bornes_s)

layout = go.Layout(plot_bgcolor='rgba(0,0,0,0)')
fig = go.Figure(layout=layout)
fig.add_trace(go.Scatter(x=mS, y=mKappa, mode='lines', line=dict(width=2)))
fig.add_trace(go.Scatter(x=mS, y=mTau, mode='lines', line=dict(width=2)))
fig.update_xaxes(showline=True, showgrid=False, linewidth=1, linecolor='black')
fig.update_yaxes(showline=True, showgrid=False, linewidth=1, linecolor='black')
for i in range(len(np.concatenate(bornes_s))):
    fig.add_vline(x=np.concatenate(bornes_s)[i], line_width=2, line_dash="dash")
fig.show()
layout = go.Layout(plot_bgcolor='rgba(0,0,0,0)')
fig = go.Figure(layout=layout)
fig.add_trace(go.Scatter(x=mS, y=mTau, mode='lines', line=dict(width=2)))
fig.update_xaxes(showline=True, showgrid=False, linewidth=1, linecolor='black')
fig.update_yaxes(showline=True, showgrid=False, linewidth=1, linecolor='black')
for i in range(len(np.concatenate(bornes_s))):
    fig.add_vline(x=np.concatenate(bornes_s)[i], line_width=2, line_dash="dash")
fig.show()
layout = go.Layout(plot_bgcolor='rgba(0,0,0,0)')
fig = go.Figure(layout=layout)
fig.add_trace(go.Scatter(x=t, y=X.Sdot(t), mode='lines', line=dict(width=2)))
fig.add_trace(go.Scatter(x=t, y=Sdotdot, mode='lines', line=dict(width=2)))
fig.update_xaxes(showline=True, showgrid=False, linewidth=1, linecolor='black')
fig.update_yaxes(showline=True, showgrid=False, linewidth=1, linecolor='black')
for i in range(len(np.concatenate(bornes))):
    fig.add_vline(x=np.concatenate(bornes)[i], line_width=2, line_dash="dash")
fig.show()

In [10]:
s_curv = [0.1199, 0.3259, 0.437, 0.662, 0.948]
s_tors = [0.438]
ind_curv = invS(s_curv)*len(data_traj)
ind_tors = invS(s_tors)*len(data_traj)
print(invS(s_curv))

part1 = data_traj[:int(ind_curv[0])]
part2 = data_traj[int(ind_curv[0]):int(ind_curv[1])]
part3 = data_traj[int(ind_curv[1]):int(ind_curv[2])]
part4 = data_traj[int(ind_curv[2]):int(ind_curv[3])]
part5 = data_traj[int(ind_curv[3]):int(ind_curv[4])]
plot_3D_means([data_traj, part1, part2, part3, part4, part5], [], " ", "")

part1 = data_traj[:int(ind_tors[0])]
part2 = data_traj[int(ind_tors[0]):]
plot_3D_means([data_traj, part1, part2], [], " ", "")


[0.31375656 0.41639068 0.51751129 0.60061028 0.77798853]
